In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
%%time

%cd /content/
%rm -rf LLaMA-Factory
!git clone https://github.com/hiyouga/LLaMA-Factory.git
%cd LLaMA-Factory
%ls
!pip install -e .[torch,bitsandbytes]
# Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"
!pip install --no-deps xformers "trl<0.9.0" peft accelerate bitsandbytes

/content
Cloning into 'LLaMA-Factory'...
remote: Enumerating objects: 15261, done.
remote: Counting objects: 100% (211/211), done.
remote: Compressing objects: 100% (91/91), done.
remote: Total 15261 (delta 128), reused 179 (delta 120), pack-reused 15050
Receiving objects: 100% (15261/15261), 221.42 MiB | 14.45 MiB/s, done.
Resolving deltas: 100% (11177/11177), done.
/content/LLaMA-Factory
assets/       docker/      LICENSE      pyproject.toml  requirements.txt  src/
CITATION.cff  evaluation/  Makefile     README.md       scripts/          tests/
data/         examples/    MANIFEST.in  README_zh.md    setup.py
Obtaining file:///content/LLaMA-Factory
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
  Using cached datasets-2.20.0-py3-none-any.whl (547 kB)
  Using cached accelerate-0.32.1-py3-none-any.whl (314 kB)
  Using cached pef

In [ ]:
import os
import sys
from pathlib import Path

workding_dir = "/content/drive/MyDrive/logical-reasoning/"
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /content/drive/MyDrive/logical-reasoning/


In [ ]:
%%time

!pip install -r requirements.txt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.9/45.9 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 337.4/337.4 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 328.3/328.3 kB 13.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.5/127.5 kB 8.1 MB/s eta 0:00:00
CPU times: user 118 ms, sys: 33.3 ms, total: 151 ms
Wall time: 14 s


In [ ]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /content/drive/MyDrive/logical-reasoning/.env


True

In [ ]:
%%time
!python --version
!pip show flash-attn

Python 3.10.12
CPU times: user 14.6 ms, sys: 1.4 ms, total: 16 ms
Wall time: 1.01 s


In [ ]:
%%time

!chmod +x ./scripts/tune-lf.sh
!./scripts/tune-lf.sh config/qwen2_7b_lora_sft.yaml

Current Directory:
/content/drive/MyDrive/logical-reasoning/llama-factory
config/qwen2_7b_lora_sft.yaml:
 {
  "model_name_or_path": "Qwen/Qwen2-7B-Instruct",
  "stage": "sft",
  "do_train": true,
  "finetuning_type": "lora",
  "lora_target": "all",
  "quantization_bit": 4,
  "loraplus_lr_ratio": 16.0,
  "dataset": "alpaca_mac",
  "template": "chatml",
  "cutoff_len": 1024,
  "max_samples": 50,
  "overwrite_cache": true,
  "preprocessing_num_workers": 16,
  "output_dir": "/content/qwen2-7b/",
  "logging_steps": 10,
  "save_steps": 10,
  "plot_loss": true,
  "overwrite_output_dir": true,
  "per_device_train_batch_size": 1,
  "gradient_accumulation_steps": 8,
  "learning_rate": 0.0001,
  "num_train_epochs": 6.0,
  "lr_scheduler_type": "cosine",
  "warmup_ratio": 0.1,
  "bf16": true,
  "ddp_timeout": 180000000,
  "val_size": 0.02,
  "per_device_eval_batch_size": 1,
  "eval_strategy": "steps",
  "eval_steps": 10,
  "report_to": "wandb",
  "run_name": "qwen2_7b_mac_colab"
}
2024-07-05 13:57:

In [ ]:
def evaluate_model_all_epochs(model_name, num_train_epochs, adapter_path_base, load_in_4bit=True):
    os.environ["MODEL_NAME"] = model_name
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    for i in range(num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{560 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path

        !python llm_toolkit/eval_lf.py

In [ ]:
%%time
num_train_epochs = 3
evaluate_model_all_epochs("Qwen/Qwen2-7B-Instruct", num_train_epochs, "/content/qwen2-7b")

Epoch 0
2024-07-05 14:35:13.920041: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-05 14:35:13.920114: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-05 14:35:13.921639: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-07-05 14:35:13.929529: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-05 14:35:15.218976: W tensorf